In [51]:
import os
from uuid import uuid4
import pandas as pd

from datasets import load_dataset
import subprocess
from transformers import AutoTokenizer

In [52]:
# from dotenv import load_dotenv,find_dotenv
# load_dotenv(find_dotenv(),override=True)

def max_token_len(dataset):
    max_seq_length = 0
    for row in dataset:
        tokens = len(tokenizer(row['text'])['input_ids'])
        if tokens > max_seq_length:
            max_seq_length = tokens
    return max_seq_length

In [53]:
# model_name='TinyLlama/TinyLlama-1.1B-Chat-v0.1'
model_name = 'mistralai/Mistral-7B-v0.1'
# model_name = 'distilbert-base-uncased'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model_max_length = tokenizer.model_max_length
print("Model Max Length:", model_max_length)

Model Max Length: 1000000000000000019884624838656


In [54]:
# Load dataset
dataset_name = 'ai-aerospace/ams_data_train_generic_v0.1_100'
dataset=load_dataset(dataset_name)

# Write dataset files into data directory
data_directory = './fine_tune_data/'

# Create the data directory if it doesn't exist
os.makedirs(data_directory, exist_ok=True)

# Write the train data to a CSV file
train_data='train_data'
train_filename = os.path.join(data_directory, train_data)
dataset['train'].to_pandas().to_csv(train_filename+'.csv', columns=['text'], index=False)
max_token_length_train=max_token_len(dataset['train'])
print('Max token length train: '+str(max_token_length_train))

# Write the validation data to a CSV file
validation_data='validation_data'
validation_filename = os.path.join(data_directory, validation_data)
dataset['validation'].to_pandas().to_csv(validation_filename+'.csv', columns=['text'], index=False)
max_token_length_validation=max_token_len(dataset['validation'])
print('Max token length validation: '+str(max_token_length_validation))
      
max_token_length=max(max_token_length_train,max_token_length_validation)
if max_token_length > model_max_length:
    raise ValueError("Maximum token length exceeds model limits.")
block_size=2*max_token_length
print('Block size: '+str(block_size))

# Define project parameters
username='ai-aerospace'
project_name='./llms/'+'ams_data_train-100_'+str(uuid4())
repo_name='ams-data-train-100-'+str(uuid4())

Max token length train: 1121
Max token length validation: 38
Block size: 2242


In [46]:
"""
This set of parameters runs on a low memory gpu on hugging face spaces:
{
  "block_size": 1024,
  "model_max_length": 2048,
  x"use_flash_attention_2": false,
  x"disable_gradient_checkpointing": false,
  "logging_steps": -1,
  "evaluation_strategy": "epoch",
  "save_total_limit": 1,
  "save_strategy": "epoch",
  x"auto_find_batch_size": false,
  "mixed_precision": "fp16",
  "lr": 0.00003,
  "epochs": 3,
  "batch_size": 2,
  "warmup_ratio": 0.1,
  "gradient_accumulation": 1,
  "optimizer": "adamw_torch",
  "scheduler": "linear",
  "weight_decay": 0,
  "max_grad_norm": 1,
  "seed": 42,
  "apply_chat_template": false,
  "quantization": "int4",
  "target_modules": "",
  x"merge_adapter": false,
  "peft": true,
  "lora_r": 16,
  "lora_alpha": 32,
  "lora_dropout": 0.05
}
"""

model_params={
  "project_name": project_name,
  "model_name": model_name,
  "repo_id": username+'/'+repo_name,
  "train_data": train_data,
  "validation_data": validation_data,
  "data_directory": data_directory,
  "block_size": block_size,
  "model_max_length": max_token_length,
  "logging_steps": -1,
  "evaluation_strategy": "epoch",
  "save_total_limit": 1,
  "save_strategy": "epoch",
  "mixed_precision": "fp16",
  "lr": 0.00003,
  "epochs": 3,
  "batch_size": 2,
  "warmup_ratio": 0.1,
  "gradient_accumulation": 1,
  "optimizer": "adamw_torch",
  "scheduler": "linear",
  "weight_decay": 0,
  "max_grad_norm": 1,
  "seed": 42,
  "quantization": "int4",
  "lora_r": 16,
  "lora_alpha": 32,
  "lora_dropout": 0.05
}
for key, value in model_params.items():
  os.environ[key] = str(value)

print(model_params)


# Save parameters to environment variables
# os.environ["project_name"] = project_name
# os.environ["model_name"] = model_name
# os.environ["repo_id"] = username+'/'+repo_name
# os.environ["train_data"] = train_data   
# os.environ["validation_data"] = validation_data
# os.environ["data_directory"] = data_directory

{'project_name': './llms/ams_data_train-100_6abb23dc-cb9d-428e-9079-e47deee0edd9', 'model_name': 'mistralai/Mistral-7B-v0.1', 'repo_id': 'ai-aerospace/ams-data-train-100-4601c8c8-0903-4f18-a6e8-1d2a40a697ce', 'train_data': 'train_data', 'validation_data': 'validation_data', 'data_directory': './fine_tune_data/', 'block_size': 2242, 'model_max_length': 1121, 'logging_steps': -1, 'evaluation_strategy': 'epoch', 'save_total_limit': 1, 'save_strategy': 'epoch', 'mixed_precision': 'fp16', 'lr': 3e-05, 'epochs': 3, 'batch_size': 2, 'warmup_ratio': 0.1, 'gradient_accumulation': 1, 'optimizer': 'adamw_torch', 'scheduler': 'linear', 'weight_decay': 0, 'max_grad_norm': 1, 'seed': 42, 'quantization': 'int4', 'lora_r': 16, 'lora_alpha': 32, 'lora_dropout': 0.05}


In [50]:

# Set .venv and execute the autotrain script
# To see all parameters: autotrain llm --help
# !autotrain llm --train --project_name my-llm --model TinyLlama/TinyLlama-1.1B-Chat-v0.1 --data_path . --use-peft --use_int4 --learning_rate 2e-4 --train_batch_size 6 --num_train_epochs 3 --trainer sft
command=f"""
autotrain llm --train \
    --trainer sft \
    --project_name {model_params['project_name']} \
    --model {model_params['model_name']} \
    --data_path {model_params['data_directory']} \
    --train_split {model_params['train_data']} \
    --valid_split {model_params['validation_data']} \
    --repo_id {model_params['repo_id']} \
    --push_to_hub \
    --token HUGGINGFACE_TOKEN \
    --block_size {model_params['block_size']} \
    --model_max_length {model_params['model_max_length']} \
    --logging_steps {model_params['logging_steps']} \
    --evaluation_strategy {model_params['evaluation_strategy']} \
    --save_total_limit {model_params['save_total_limit']} \
    --save_strategy {model_params['save_strategy']} \
    --fp16 \
    --lr {model_params['lr']} \
    --num_train_epochs {model_params['epochs']} \
    --train_batch_size {model_params['batch_size']} \
    --warmup_ratio {model_params['warmup_ratio']} \
    --gradient_accumulation {model_params['gradient_accumulation']} \
    --optimizer {model_params['optimizer']} \
    --scheduler linear \
    --weight_decay {model_params['weight_decay']} \
    --max_grad_norm {model_params['max_grad_norm']} \
    --seed {model_params['seed']} \
    --use_int4 \
    --use-peft \
    --lora_r {model_params['lora_r']} \
    --lora_alpha {model_params['lora_alpha']} \
    --lora_dropout {model_params['lora_dropout']}
"""

# Use subprocess.run() to execute the command
subprocess.run(command, shell=True, check=True)

⚠️ WARNING | 2023-12-22 10:41:00 | autotrain.cli.run_dreambooth:<module>:14 - ❌ Some DreamBooth components are missing! Please run `autotrain setup` to install it. Ignore this warning if you are not using DreamBooth or running `autotrain setup` already.
Traceback (most recent call last):
  File "/home/dsmueller/Repositories/HuggingFace/autotrain-playground/.venv/bin/autotrain", line 8, in <module>
    sys.exit(main())
             ^^^^^^
  File "/home/dsmueller/Repositories/HuggingFace/autotrain-playground/.venv/lib/python3.11/site-packages/autotrain/cli/autotrain.py", line 47, in main
    command = args.func(args)
              ^^^^^^^^^^^^^^^
  File "/home/dsmueller/Repositories/HuggingFace/autotrain-playground/.venv/lib/python3.11/site-packages/autotrain/cli/run_llm.py", line 14, in run_llm_command_factory
    return RunAutoTrainLLMCommand(args)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/dsmueller/Repositories/HuggingFace/autotrain-playground/.venv/lib/python3.11/site-pac

CalledProcessError: Command '
autotrain llm --train     --trainer sft     --project_name ./llms/ams_data_train-100_6abb23dc-cb9d-428e-9079-e47deee0edd9     --model mistralai/Mistral-7B-v0.1     --data_path ./fine_tune_data/     --train_split train_data     --valid_split validation_data     --repo_id ai-aerospace/ams-data-train-100-4601c8c8-0903-4f18-a6e8-1d2a40a697ce     --push_to_hub     --token HUGGINGFACE_TOKEN     --block_size 2242     --model_max_length 1121     --logging_steps -1     --evaluation_strategy epoch     --save_total_limit 1     --save_strategy epoch     --fp16     --lr 3e-05     --num_train_epochs 3     --train_batch_size 2     --warmup_ratio 0.1     --gradient_accumulation 1     --optimizer adamw_torch     --scheduler linear     --weight_decay 0     --max_grad_norm 1     --seed 42     --use_int4     --use-peft     --lora_r 16     --lora_alpha 32     --lora_dropout 0.05
' returned non-zero exit status 1.